In [35]:
# Работа с табличными данными

import pandas as pd
import numpy as np


# Визуализация

import plotly.express as px
import plotly.io as pio
pio.templates.default = 'plotly_dark'
pio.renderers.default = 'notebook'
from motorica.emg8.utils import fig_montage # кастомная функция визуализации


# Пайплайн

# чтение данных и разметка по фактическим жестам
from motorica.emg8.pipeline import read_emg8
from motorica.emg8.markers import BasePeakMarker, TransMarker
# создание экземпляра пайплайна на базе: 
from motorica.emg8.pipeline import create_logreg_pipeline # логистической регрессии
# константы
from motorica.emg8.constants import *


# Метрики
from sklearn.metrics import classification_report


# Для вывода докстрингов с форматированием markdown
from IPython.display import Markdown as md

# Работа с файлами
import os

# Для оценки скорости инференса
from time import time

# Сериализация модели (пайплайна)
import pickle

## Подгрузка и разметка данных

Список имеющихся файлов с данными:

In [36]:
# Папка с файлами данных
DATA_DIR = 'data/meeting'

montages = sorted(filter(lambda f: f.endswith('.emg8'), os.listdir(DATA_DIR)))
montages

['2024-12-12_11-31-04-artemiy.emg8',
 '2024-12-12_12-33-40-oleg.emg8',
 '2024-12-12_14-16-16.emg8',
 '2024-12-12_14-36-51.emg8']

In [37]:
montage = montages[0]
gestures_raw = pd.read_csv(os.path.join(DATA_DIR, montage), sep=' ')
fig_montage(
    gestures_raw[OMG_CH], y_cmd=gestures_raw['id'], 
    title=f"<i>{montage}</i> – исходные данные"
).show()

In [38]:
trans_marker = TransMarker(use_peaks='std')
X_train, X_test, y_train, y_test, gestures, cv_groups = read_emg8(
    montage, dir=DATA_DIR,
    n_holdout_groups=1,
    marker=trans_marker
)

print('X_train shape:', X_train.shape)
print('y_train shape:', y_train.shape)
print('X_test shape:', X_test.shape)
print('y_test shape:', y_test.shape)

state_id = gestures[['id', 'state']].drop_duplicates()
GESTURES = state_id['state'] + ' ' + state_id['id'].astype(str)
display(GESTURES)

fig_montage(
    gestures[OMG_CH], 
    y_cmd=gestures[CMD_COL], 
    y_act=gestures[TARGET],
    protocol_cycle=gestures[GROUP_COL],
    # grad2=marker.peaks_grad2 / 2,
    # grad2_neg=marker.peaks_grad2_neg / 2,
    # std1=marker.peaks_std1 / 2,
    # std1_neg=marker.peaks_std1_neg / 2,
    title=f"<i>{montage}</i> – разметка переходов"
).show()

X_train shape: (4366, 16)
y_train shape: (4366,)
X_test shape: (1134, 16)
y_test shape: (1134,)


125          Neutral 0
225     ThumbFingers 1
375            Close 2
525             Open 3
675            Pinch 4
825       Indication 5
975       Wrist_Flex 6
1125    Wrist_Extend 7
dtype: object

В качестве отложенной выборки оставим последний цикл протокола:

In [39]:
n_holdout_groups = 1 # отложенная выборка - последний цикл протокола

marker = BasePeakMarker()

X_train, X_test, y_train, y_test, gestures, cv_groups = read_emg8(
    montage, dir=DATA_DIR,
    n_holdout_groups=n_holdout_groups,
    marker=marker
)

last_train_idx = gestures[GROUP_COL].drop_duplicates().index[-n_holdout_groups] - 1

print('X_train shape:', X_train.shape)
print('y_train shape:', y_train.shape)
print('X_test shape:', X_test.shape)
print('y_test shape:', y_test.shape)

state_id = gestures[['id', 'state']].drop_duplicates()
GESTURES = state_id['state'] + ' ' + state_id['id'].astype(str)
display(GESTURES)

fig_montage(
    gestures[OMG_CH], 
    y_cmd=gestures[CMD_COL], 
    y_act=gestures[TARGET],
    protocol_cycle=gestures[GROUP_COL],
    # grad2=marker.peaks_grad2 / 2,
    # grad2_neg=marker.peaks_grad2_neg / 2,
    # std1=marker.peaks_std1 / 2,
    # std1_neg=marker.peaks_std1_neg / 2,
    title=f"<i>{montage}</i> – разметка по фактическим границам жестов"
).show()

X_train shape: (4356, 16)
y_train shape: (4356,)
X_test shape: (1144, 16)
y_test shape: (1144,)


125          Neutral 0
225     ThumbFingers 1
375            Close 2
525             Open 3
675            Pinch 4
825       Indication 5
975       Wrist_Flex 6
1125    Wrist_Extend 7
dtype: object

## Пайплайн

In [40]:
model = create_logreg_pipeline(optimize=False, X=X_train, y=y_train, groups=cv_groups)#, groups=cv_groups)
model

Pipeline(steps=[('fix_1dim_sample', FixOneDimSample()),
                ('noise_reduct', NoiseReduction()),
                ('add_diff', AddDifference(n_lags=5)),
                ('scaler', MinMaxScaler()), ('model', PostprocWrapper())])

In [41]:
# сохранение пайплайна (сериализация)
with open('pipeline_logreg.pkl', 'wb') as f:
    pickle.dump(model, f)

# восстановление пайплайна из файла
with open('pipeline_logreg.pkl', 'rb') as f:
    model = pickle.load(f)

In [42]:
y_train_pred = model.predict(X_train)
y_test_pred = model.predict(X_test)

In [43]:
print("Train data " + '-' * 44)
print(classification_report(y_train, y_train_pred, target_names=GESTURES))

Train data --------------------------------------------
                precision    recall  f1-score   support

     Neutral 0       0.93      0.96      0.94      3251
ThumbFingers 1       0.87      0.65      0.75       168
       Close 2       0.90      0.86      0.88       147
        Open 3       0.87      0.83      0.85       173
       Pinch 4       0.83      0.49      0.61       152
  Indication 5       0.86      0.84      0.85       168
  Wrist_Flex 6       0.85      0.91      0.88       136
Wrist_Extend 7       0.90      0.88      0.89       161

      accuracy                           0.91      4356
     macro avg       0.88      0.80      0.83      4356
  weighted avg       0.91      0.91      0.91      4356



In [44]:
print("Test data " + '-' * 45)
print(classification_report(y_test, y_test_pred, target_names=GESTURES))

Test data ---------------------------------------------
                precision    recall  f1-score   support

     Neutral 0       0.95      0.95      0.95       865
ThumbFingers 1       0.94      0.76      0.84        45
       Close 2       0.77      0.73      0.75        33
        Open 3       0.78      0.87      0.82        45
       Pinch 4       0.85      0.81      0.83        36
  Indication 5       0.81      0.87      0.84        45
  Wrist_Flex 6       0.88      0.91      0.90        33
Wrist_Extend 7       0.79      0.88      0.83        42

      accuracy                           0.92      1144
     macro avg       0.85      0.85      0.84      1144
  weighted avg       0.92      0.92      0.92      1144



## Симуляция инференса в реальном времени на отложенной выборке

In [45]:
y_test_pred = np.empty(0)
comp_durations = np.empty(0)

for i in range(X_test.shape[0]):
    start_time = time()
    #y_test_pred = np.append(y_test_pred, model.predict(X_test[i].reshape(1, -1)))
    y_test_pred = np.append(y_test_pred, model.predict(X_test[i]))
    comp_duration = time() - start_time
    comp_durations = np.append(comp_durations, comp_duration)

print(f"Максимальное время: {np.round(comp_durations.max() * 1000, 2)} мс")
print(f"Среднее время: {np.round(comp_durations.mean() * 1000, 2)} мс")

fig = px.scatter(
    comp_durations * 1000, color=y_test_pred, width=1000, height=500,
    title='Время инференса при последовательных предсказаниях примеров тестовой выборки',
    labels={'value': 'время, мс'}
)
fig.update_coloraxes(showscale=False)
fig.show()

print(classification_report(y_test, y_test_pred, target_names=GESTURES))

fig = fig_montage(
    pd.DataFrame(X_test), 
    y_cmd=gestures.loc[last_train_idx + 1:, CMD_COL].reset_index(drop=True), 
    y_true=y_test, y_pred=y_test_pred,
    title=f"{montage}<br>Результаты последовательных предсказаний примеров тестовой выборки"
)
fig.show()

Максимальное время: 3.85 мс
Среднее время: 0.33 мс


                precision    recall  f1-score   support

     Neutral 0       0.95      0.95      0.95       865
ThumbFingers 1       0.94      0.76      0.84        45
       Close 2       0.77      0.73      0.75        33
        Open 3       0.78      0.87      0.82        45
       Pinch 4       0.85      0.81      0.83        36
  Indication 5       0.81      0.87      0.84        45
  Wrist_Flex 6       0.88      0.91      0.90        33
Wrist_Extend 7       0.82      0.88      0.85        42

      accuracy                           0.92      1144
     macro avg       0.85      0.85      0.85      1144
  weighted avg       0.92      0.92      0.92      1144

